## 0. Goal
Apply the trained UMAP model to all sorted audio data to obtain UMAP embeddings of certain syllable types, or all types

In [18]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "0"

In [19]:
import os, sys, importlib, librosa, glob, h5py, tqdm, pickle, gc, shutil
from scipy.io import wavfile
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from joblib import Parallel, delayed
import random
import umap, hdbscan
from collections import Counter, OrderedDict
import seaborn as sns
from torch.utils.data import Dataset, DataLoader, TensorDataset
import torch
from matplotlib.colors import ListedColormap
from matplotlib.patches import Patch
from skimage import transform
import gc

plt.rcParams['pdf.fonttype'] = 42 

In [20]:
# import my utility script
cluster_script_path = '/home/zz367/ProjectsU/EphysMONAO/Jupyter/MatlabCodes/ZZ_callClustering/'
sys.path.insert(1, cluster_script_path)
import vae_goffinet, hopkins
importlib.reload(vae_goffinet)

<module 'vae_goffinet' from '/home/zz367/ProjectsU/EphysMONAO/Jupyter/MatlabCodes/ZZ_callClustering/vae_goffinet.py'>

In [21]:
# create a custom colormap for spectrogram
jet = plt.get_cmap('jet', 255)
# Extract jet colors and prepend black at the beginning
jet_colors = jet(np.linspace(0, 1, 255))
custom_colors = np.vstack([[0, 0, 0, 1], jet_colors])  # Black for 0, then jet
custom_cmap = ListedColormap(custom_colors)

## 1. Inputs

In [22]:
fd_z4 = '/mnt/z4'
fd_data = os.path.join(fd_z4, 'zz367', 'EphysMONAO', 'Analyzed', 'vaeWav')
birdID = 'pair5RigCCU29'
# where are wav files and segmentation located
fd_save_base = os.path.join(fd_data, birdID, 'Traj', 'applySylAll')
# what run of VAE to use
vae_run = 'traj_chop_32_1_32'
# where the latent features are stored
fd_latent = os.path.join(fd_save_base, f'latents.{vae_run}')
fn_latent = os.path.join(fd_latent, f'{birdID}.latents.{vae_run}.h5')
fn_latent_info = os.path.join(fd_latent, f'{birdID}.latents.{vae_run}.info.csv')
info = pd.read_csv(fn_latent_info, index_col=0)
print(info.shape)
# how large is sliding window
win_frame = 32

(92140, 23)


In [23]:
# what umap model to use
fd_umap = os.path.join(fd_data, birdID, 'Traj', 'applySyl5', 'paramSearch5_r2', vae_run)
umap_run = 'paired.v4v5'
# umap_run = 'paired.v1v7'
# umap_run = 'all.v0v1v2v3v4v5v6v7'
fn_umap = os.path.join(fd_umap, f'UMAPmodel_pair5RigCCU29.{umap_run}.p')
# what syllables can be analyzed by this umap model
syl = ['v4', 'v5']
# syl = ['v1', 'v7']
# syl = ['v0', 'v1', 'v2', 'v3', 'v4', 'v5', 'v6', 'v7']
print('Using UMAP model: ', fn_umap, 'for', syl)

Using UMAP model:  /mnt/z4/zz367/EphysMONAO/Analyzed/vaeWav/pair5RigCCU29/Traj/applySyl5/paramSearch5_r2/traj_chop_32_1_32/UMAPmodel_pair5RigCCU29.paired.v4v5.p for ['v4', 'v5']


## 2. Apply the trained UMAP model

In [24]:
# where to save UMAP results
fd_save = os.path.join(fd_save_base, f'umap.{umap_run}')
if not os.path.exists(fd_save):
    os.makedirs(fd_save)
print('Saving UMAP results to: ', fd_save)

Saving UMAP results to:  /mnt/z4/zz367/EphysMONAO/Analyzed/vaeWav/pair5RigCCU29/Traj/applySylAll/umap.paired.v4v5


In [25]:
# load the UMAP model
with open(fn_umap, 'rb') as f:
    UMAP_model = pickle.load(f)

Mon Aug  4 21:12:41 2025 Building and compiling search function


In [26]:
# save UMAP results again as h5
fn_embed = os.path.join(fd_save, f'{birdID}.{vae_run}.{umap_run}.h5')
print('Save embeddings as h5 file: ', fn_embed)

Save embeddings as h5 file:  /mnt/z4/zz367/EphysMONAO/Analyzed/vaeWav/pair5RigCCU29/Traj/applySylAll/umap.paired.v4v5/pair5RigCCU29.traj_chop_32_1_32.paired.v4v5.h5


In [10]:
# loop through syllables, apply UMAP model if it's the desired syllable types
with h5py.File(fn_embed, 'w') as h5f:
    for si in tqdm.tqdm(range(info.shape[0])):
    # for si in range(83749, 83750):
        syl_id = info['syl_ID'][si]
        v = info['call_subtype'][si]
        if pd.isna(v):
            v = info['label'][si]
        if v in syl:
            with h5py.File(fn_latent, 'r') as f:
                d = f[syl_id][:]
            res = UMAP_model.transform(d)
            h5f.create_dataset(syl_id, data=res, compression='gzip')

  0%|          | 0/92140 [00:00<?, ?it/s]

Epochs completed:   0%|            0/100 [00:00]

  1%|          | 691/92140 [00:02<06:32, 232.71it/s]

	completed  0  /  100 epochs
	completed  10  /  100 epochs
	completed  20  /  100 epochs
	completed  30  /  100 epochs
	completed  40  /  100 epochs
	completed  50  /  100 epochs
	completed  60  /  100 epochs
	completed  70  /  100 epochs
	completed  80  /  100 epochs
	completed  90  /  100 epochs


Epochs completed:   0%|            0/100 [00:00]

...

100%|█████████▉| 92081/92140 [48:09<00:01, 30.48it/s]

	completed  0  /  100 epochs
	completed  10  /  100 epochs
	completed  20  /  100 epochs
	completed  30  /  100 epochs
	completed  40  /  100 epochs
	completed  50  /  100 epochs
	completed  60  /  100 epochs
	completed  70  /  100 epochs
	completed  80  /  100 epochs
	completed  90  /  100 epochs


Epochs completed:   0%|            0/100 [00:00]

100%|██████████| 92140/92140 [48:10<00:00, 31.88it/s]

	completed  0  /  100 epochs
	completed  10  /  100 epochs
	completed  20  /  100 epochs
	completed  30  /  100 epochs
	completed  40  /  100 epochs
	completed  50  /  100 epochs
	completed  60  /  100 epochs
	completed  70  /  100 epochs
	completed  80  /  100 epochs
	completed  90  /  100 epochs


In [41]:
## save results as csv instead, so can be visualized in EmbedViewer
def applyUMAP_v1(syl_id):
    with h5py.File(fn_latent, 'r') as f:
        d = f[syl_id][:]
    res = UMAP_model.transform(d)
    return(res)

In [42]:
syl_apply = [info['syl_ID'][ii] for ii in info.index if info['call_subtype'][ii] in syl]

In [43]:
with Parallel(n_jobs=48, verbose=5, backend='loky') as parallel:
    res = parallel(delayed(applyUMAP_v1)(syl_id) for syl_id in syl_apply)

[Parallel(n_jobs=48)]: Using backend LokyBackend with 48 concurrent workers.


Mon Aug  4 21:21:04 2025 Building and compiling search function
Mon Aug  4 21:21:05 2025 Building and compiling search function
Mon Aug  4 21:21:05 2025 Building and compiling search function
Mon Aug  4 21:21:05 2025 Building and compiling search function
Mon Aug  4 21:21:06 2025 Building and compiling search function
Mon Aug  4 21:21:06 2025 Building and compiling search function
Mon Aug  4 21:21:06 2025 Building and compiling search function
Mon Aug  4 21:21:06 2025 Building and compiling search function
Mon Aug  4 21:21:07 2025 Building and compiling search function


BrokenProcessPool: A task has failed to un-serialize. Please ensure that the arguments of the function are all picklable.

In [31]:
res.shape

(313, 2)